In [1]:
from random import sample, seed
import numpy as np 
import pandas as pd

#utility functions : prepare the data 
from model_fp_selection.lib.utils import get_morgan_fp, get_rdkit_fp, convert_to_float, get_rdkit_fp_from_smiles
from model_fp_selection.lib.utils import prepare_df_morgan, prepare_df_rdkit, swap_identical_ligands
from model_fp_selection.lib.utils import drop_duplicates, average_duplicates, calc_desc

# RDkit
from rdkit import Chem, RDLogger
from rdkit.Chem import AllChem, DataStructs, Draw, rdMolDescriptors
from rdkit.Chem.Scaffolds import MurckoScaffold
from rdkit.Chem.rdDepictor import Compute2DCoords

# Visualization
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 20})

import mols2grid
import requests
import os

# Combinatorial library generation
import itertools
from itertools import combinations_with_replacement

from tqdm.auto import tqdm
import time

np.random.seed(42)
seed(42)

In [55]:
best_desc = pd.read_csv('c:/Users/CTMguest/Desktop/csv_results/best_complexes_10k_desc.csv')

In [33]:
best_fp = pd.read_csv('c:/Users/CTMguest/Desktop/csv_results/complexes_ucb_10k_best_fp.csv')

In [56]:
best_desc['FP1'] = best_desc['L1'].apply(Chem.MolFromSmiles)
best_desc['FP1'] = best_desc['FP1'].apply(lambda mol: get_rdkit_fp(mol, nbits=2048))

In [57]:
best_desc['FP2'] = best_desc['L2'].apply(Chem.MolFromSmiles)
best_desc['FP2'] = best_desc['FP2'].apply(lambda mol: get_rdkit_fp(mol, nbits=2048))

In [58]:
best_desc['FP3'] = best_desc['L3'].apply(Chem.MolFromSmiles)
best_desc['FP3'] = best_desc['FP3'].apply(lambda mol: get_rdkit_fp(mol, nbits=2048))

In [59]:
best_desc['Fingerprint'] = best_desc['FP1'] + best_desc['FP2'] + best_desc['FP3']

In [38]:
best_fp['FP1'] = best_desc.L1.apply(Chem.MolFromSmiles)
best_fp['FP2'] = best_desc.L2.apply(Chem.MolFromSmiles)
best_fp['FP3'] = best_desc.L3.apply(Chem.MolFromSmiles)

best_fp['FP1'] = best_fp['FP1'].apply(lambda mol: get_rdkit_fp(mol, nbits=2048))
best_fp['FP2'] = best_fp['FP2'].apply(lambda mol: get_rdkit_fp(mol, nbits=2048))
best_fp['FP3'] = best_fp['FP3'].apply(lambda mol: get_rdkit_fp(mol, nbits=2048))
best_fp['Fingerprint'] = best_fp['FP1'] + best_fp['FP2'] + best_fp['FP3']

### Distance to the original dataset

In [39]:
def tanimoto_distance(vector1, vector2):
    dot_product = np.dot(vector1, vector2)
    norm_squared_a = np.dot(vector1, vector1)
    norm_squared_b = np.dot(vector2, vector2)
    
    tanimoto_dist = 1 - dot_product / (norm_squared_a + norm_squared_b - dot_product)
    
    return tanimoto_dist


In [40]:
def get_distances(df, fingerprint1, distance, desc = False): 
    """
    Returns the list of distances between a complex and the complexes of the dataset.
    param : dataset : a dataframe with a column 'Fingerprint'
    param : fingerprint1: the fingerprint of the generated compound
    param : distance : the name of the distance to be used, either cosine_distance or tanimoto_distance
    return : a list of floats (the distances)
    """

    distances = []

    for index, row in df.iterrows():
        
        if desc == True : 
            fingerprint2 = row['Descriptors']
        else : 
            fingerprint2 = row['Fingerprint']
        
        dis = distance(fingerprint1, fingerprint2)
        if dis != 0 : 
            distances.append(dis)
      
    return distances

In [41]:
def get_minimal_distances_dataset(df, dataset, distance, desc = False): 
    """
    Returns the list of minimal distances between each complex of the dataset and the rest of the complexes.
    param : df : the dataframe of generated compounds 
    param : dataset : the dataframe of the original dataset of compounds. 
    param : distance : the name of the distance to be used, either cosine_distance or tanimoto_distance
    return : a list of floats (the distances).
    """
    
    minimal_distances = []
    
    for index, row in df.iterrows():
        if desc == True : 
            fingerprint = row['Descriptors']
            #we get the distance between a complexe to-be-tested and the entire dataset
            list = get_distances(dataset, fingerprint, distance, desc = True)
            if len(list) !=0 :
                minimal_distance = min(list) 
                minimal_distances.append(minimal_distance)
        else : 
            fingerprint = row['Fingerprint']
            #we get the distance between a complexe to-be-tested and the entire dataset
            minimal_distance = min(get_distances(dataset, fingerprint, distance)) 
            minimal_distances.append(minimal_distance)
        
    return minimal_distances

In [42]:
def get_mean_distances_dataset(df, dataset, distance, desc = False): 
    """
    Returns the list of mean distances between each complex of the dataset and the rest of the complexes.
    param : df : the dataframe of generated compounds 
    param : dataset : the dataframe of the original dataset of compounds. 
    param : distance : the name of the distance to be used, either cosine_distance or tanimoto_distance
    return : a list of floats (the distances).
    """
    
    mean_distances = []
    
    for index, row in df.iterrows():
        if desc == True : 
            fingerprint = row['Descriptors']
            #we get the distance between a complexe to-be-tested and the entire dataset
            list_dist = get_distances(dataset, fingerprint, distance, desc = True)
            if len(list) !=0 :
                mean_distance = np.mean(list_dist) 
                mean_distances.append(mean_distance)
        else : 
            fingerprint = row['Fingerprint']
            #we get the distance between a complexe to-be-tested and the entire dataset
            mean_distance = np.mean(get_distances(dataset, fingerprint, distance)) 
            mean_distances.append(mean_distance)
        
    return mean_distances

In [43]:
metals = pd.read_csv('ruthenium_complexes_dataset.csv')
metals = prepare_df_rdkit(metals)
metals

L1  \
0         C[N+](C)(C)Cc1ccnc(-c2cc(C[N+](C)(C)C)ccn2)c1   
1     CC[N+](CC)(CC)Cc1ccnc(-c2cc(C[N+](CC)(CC)CC)cc...   
2     CCCC[N+](CCCC)(CCCC)Cc1ccnc(-c2cc(C[N+](CCCC)(...   
3            c1ccc(-c2ccnc3c2ccc2c(-c4ccccc4)ccnc23)cc1   
4            c1ccc(-c2ccnc3c2ccc2c(-c4ccccc4)ccnc23)cc1   
...                                                 ...   
2966                                c1ccc(-c2ccccn2)nc1   
2967                                c1ccc(-c2ccccn2)nc1   
2968                                c1ccc(-c2ccccn2)nc1   
2969                                c1ccc(-c2ccccn2)nc1   
2970                                c1ccc(-c2ccccn2)nc1   

                                                     L2  \
0         C[N+](C)(C)Cc1ccnc(-c2cc(C[N+](C)(C)C)ccn2)c1   
1     CC[N+](CC)(CC)Cc1ccnc(-c2cc(C[N+](CC)(CC)CC)cc...   
2     CCCC[N+](CCCC)(CCCC)Cc1ccnc(-c2cc(C[N+](CCCC)(...   
3            c1ccc(-c2ccnc3c2ccc2c(-c4ccccc4)ccnc23)cc1   
4            c1ccc(-c2ccnc3c2ccc2c(-c4ccccc4)ccnc23)cc1   
...                                                 ...   
2966                                c1ccc(-c2ccccn2)nc1   
2967                                c1ccc(-c2ccccn2)nc1   
2968                                c1ccc(-c2ccccn2)nc1   
2969                                c1ccc(-c2ccccn2)nc1   
2970                                c1ccc(-c2ccccn2)nc1   

                                                     L3  Charge  \
0         C[N+](C)(C)Cc1ccnc(-c2cc(C[N+](C)(C)C)ccn2)c1       8   
1     CC[N+](CC)(CC)Cc1ccnc(-c2cc(C[N+](CC)(CC)CC)cc...       8   
2     CCCC[N+](CCCC)(CCCC)Cc1ccnc(-c2cc(C[N+](CCCC)(...       8   
3                   Cc1ccnc(-c2cc(C(=O)NCCCCCCN)ccn2)c1       2   
4                   Cc1ccnc(-c2cc(C(=O)NCCCCCCN)ccn2)c1       2   
...                                                 ...     ...   
2966      C(#Cc1ccc2nc3c4cccnc4c4ncccc4c3nc2c1)c1ccccc1       2   
2967      C(#Cc1ccc2nc3c4cccnc4c4ncccc4c3nc2c1)c1ccccc1       2   
2968      C(#Cc1ccc2nc3c4cccnc4c4ncccc4c3nc2c1)c1ccccc1       2   
2969      C(#Cc1ccc2nc3c4cccnc4c4ncccc4c3nc2c1)c1ccccc1       2   
2970      C(#Cc1ccc2nc3c4cccnc4c4ncccc4c3nc2c1)c1ccccc1       2   

                             DOI   logP       Cells     Localisation  \
0         10.1002/anie.201507800  -3.54        HeLa          lysosom   
1         10.1002/anie.201507800  -3.05        HeLa          lysosom   
2         10.1002/anie.201507800  -1.55        HeLa          lysosom   
3         10.1002/anie.201916400    NaN        HeLa  golgi apparatus   
4         10.1002/anie.201916400    NaN       RPE-1  golgi apparatus   
...                          ...    ...         ...              ...   
2966  10.1016/j.csbj.2018.11.010  -0.87  MDA-MB-231          nucleus   
2967  10.1016/j.csbj.2018.11.010  -0.87        A549          nucleus   
2968  10.1016/j.csbj.2018.11.010  -0.87       MCF.7          nucleus   
2969  10.1016/j.csbj.2018.11.010  -0.87       HepG2          nucleus   
2970  10.1016/j.csbj.2018.11.010  -0.87       HaCat          nucleus   

      IncubationTime    IC50  ...  \
0                4.0  470.00  ...   
1                4.0  425.00  ...   
2                4.0  301.00  ...   
3                4.0   13.57  ...   
4                4.0    4.22  ...   
...              ...     ...  ...   
2966            72.0   17.20  ...   
2967            72.0   20.00  ...   
2968            72.0   74.90  ...   
2969            72.0    9.75  ...   
2970            72.0   47.20  ...   

                                                   MOL3  \
0     <rdkit.Chem.rdchem.Mol object at 0x000001D9939...   
1     <rdkit.Chem.rdchem.Mol object at 0x000001D9939...   
2     <rdkit.Chem.rdchem.Mol object at 0x000001D9939...   
3     <rdkit.Chem.rdchem.Mol object at 0x000001D9939...   
4     <rdkit.Chem.rdchem.Mol object at 0x000001D9939...   
...                                                 ...   
2966  <rdkit.Chem.rdchem.Mol object at 0x000001D9FFB...   
2967  <rdkit.Chem.rdchem.Mol object at 0x000001D

In [44]:
metals['Fingerprint'] = metals.Fingerprint.apply(np.array)

In [60]:
min_dist = get_minimal_distances_dataset(best_desc, metals, tanimoto_distance)

In [61]:
best_desc['min_dist'] = np.array(min_dist)

In [62]:
mean_dist = get_mean_distances_dataset(best_desc, metals, tanimoto_distance)

In [63]:
best_desc['mean_dist'] = np.array(mean_dist)

### Adding fingerprint prediction

In [49]:
best_fp.drop(['prediction 8026', 'variance 8026', 'ucb 8026'], axis=1, inplace=True)

In [64]:
pred_fp = []
variance_fp = []
ucb_fp = []
for fp1 in best_desc.Fingerprint.values.tolist():
    for i, row in best_fp.iterrows():
        if tanimoto_distance(fp1, row['Fingerprint']) == 0:
            pred = row['prediction 1533']
            var = row['variance 1533']
            ucb = row['ucb 1533']
            pred_fp.append(pred)
            variance_fp.append(var)
            ucb_fp.append(ucb)

best_desc['pred_fp'] = np.array(pred_fp)
best_desc['variance_fp'] = np.array(variance_fp)
best_desc['ucb_fp'] = np.array(ucb_fp)

### Displaying molecules and relevant information

In [65]:
best_desc = best_desc.rename(columns={'prediction 1533' : 'pred_desc', 'variance 1533' : 'variance_desc', 'ucb 1533' : 'ucb_desc'})

In [66]:
best_desc['SMILES'] = best_desc.L1 + '.' + best_desc.L2 + '.' + best_desc.L3
best_desc['mol'] = best_desc['SMILES'].apply(Chem.MolFromSmiles)

In [67]:
subset = ['ucb_desc', 'ucb_fp', 'pred_desc', 'pred_fp', 'min_dist', 'mean_dist']

for col in subset:
    best_desc[col] = best_desc[col].round(2)
    best_desc[col] = best_desc[col].apply(lambda x: f"{col}: {x}")

In [68]:
mols2grid.display(best_desc, mol_col='mol', subset=subset, size=(300,300))

MolGridWidget()

In [69]:
mols2grid.save(best_desc, mol_col='mol', subset=subset, size=(300,300), output="best_results_grid.html")

MolGridWidget()

In [52]:
from rdkit.Chem.Draw import MolsToGridImage
from PIL import Image
subset = ['ucb_desc', 'ucb_fp', 'pred_desc', 'pred_fp', 'min_dist', 'mean_dist']

def format_values(row):
    return '\n'.join([f"{col}: {row[col]}" for col in subset])

best_desc['Numerical Values'] = best_desc.apply(format_values, axis=1)

image = MolsToGridImage(best_desc['mol'], molsPerRow=3, legends=best_desc['Numerical Values'].tolist(), subImgSize=(800,800), maxMols=100, returnPNG=False)
image

In [53]:
image.save("molecule_grid_image.png")